## Libraries Imported for this exercise

In [69]:
import numpy as np

import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json

from geopy.geocoders import Nominatim

import requests

import io

from pandas.io.json import json_normalize 

import matplotlib.cm as cm

import matplotlib.colors as colors

from sklearn.cluster import KMeans

import folium

print('Libraries imported.')

Libraries imported.


# 1) Creating the Toronto Neighborhoods Dataframe

The initial step of this process involves scraping the Wikipedia page 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:M' in order to obtain the data that is in the table of postal codes and to transform the data into a pandas dataframe.

## Assumptions

1) The dataframe consists of only three columns: PostalCode, Borough, and Neighborhood.

2) The only cells that have been processed are cells that have an assigned borough. Cells with a borough that is Not assigned have been ignored.

3) More than one neighborhood can exist in one postal code area.

4) If a cell has a borough but a Not assigned neighborhood, then the neighborhood will be the same as the borough.

In [33]:
url = requests.get('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M').text

In [65]:
toronto_data = pd.read_html(url, header = 0)[0]
toronto_data.head(10)

Postcode           Borough     Neighbourhood
0      M1A      Not assigned      Not assigned
1      M2A      Not assigned      Not assigned
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront
5      M6A        North York  Lawrence Heights
6      M6A        North York    Lawrence Manor
7      M7A      Queen's Park      Not assigned
8      M8A      Not assigned      Not assigned
9      M9A      Queen's Park      Queen's Park

In [66]:
toronto_data = toronto_data[toronto_data.Borough != 'Not assigned']
toronto_data = toronto_data.rename(columns={'Postcode': 'PostalCode'})

for index, row in toronto_data.iterrows():
    if row['Neighbourhood'] == 'Not assigned':
        row['Neighbourhood'] = row['Borough']


toronto_data.head(10)

PostalCode           Borough     Neighbourhood
2         M3A        North York         Parkwoods
3         M4A        North York  Victoria Village
4         M5A  Downtown Toronto      Harbourfront
5         M6A        North York  Lawrence Heights
6         M6A        North York    Lawrence Manor
7         M7A      Queen's Park      Queen's Park
9         M9A      Queen's Park      Queen's Park
10        M1B       Scarborough             Rouge
11        M1B       Scarborough           Malvern
13        M3B        North York   Don Mills North

In [90]:
print('The dataframe has the following rows and columns: ', toronto_data.shape)

The dataframe has the following rows and columns:  (210, 3)


# 2) Adding Coordinates to the Toronto Neighborhoods Dataframe

The next step is to add the longitudinal and latitudinal coordinates to the neighborhoods in the datafame using data provided in the csv file (http://cocl.us/Geospatial_data).

In [71]:
coordinates = "https://cocl.us/Geospatial_data"

neighborhood_latlon = requests.get(coordinates).text
neighborhood_latlon_data = pd.read_csv(io.StringIO(neighborhood_latlon))

neighborhood_latlon_data.head(10)

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476
5         M1J  43.744734 -79.239476
6         M1K  43.727929 -79.262029
7         M1L  43.711112 -79.284577
8         M1M  43.716316 -79.239476
9         M1N  43.692657 -79.264848

In [79]:
#The reference column 'Postal Code' should be renamed to match the same format as column 'PostalCode' in the first dataframe

neighborhood_latlon_data = neighborhood_latlon_data.rename(columns={'Postal Code': 'PostalCode'})
neighborhood_latlon_data.head()

PostalCode   Latitude  Longitude
0        M1B  43.806686 -79.194353
1        M1C  43.784535 -79.160497
2        M1E  43.763573 -79.188711
3        M1G  43.770992 -79.216917
4        M1H  43.773136 -79.239476

In [80]:
toronto_dataframe = pd.merge(toronto_data, neighborhood_latlon_data, on='PostalCode')
toronto_dataframe.head()

PostalCode           Borough     Neighbourhood   Latitude  Longitude
0        M3A        North York         Parkwoods  43.753259 -79.329656
1        M4A        North York  Victoria Village  43.725882 -79.315572
2        M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636
3        M6A        North York  Lawrence Heights  43.718518 -79.464763
4        M6A        North York    Lawrence Manor  43.718518 -79.464763

# 3) Exploring and Clustering Neighborhoods in Toronto

## 3.1) Exploring Downtown Toronto

Now that we have the coordinates for each borough and neighborhood, we can now explore venues in Toronto.

In [121]:
address = 'Toronto'

geolocator = Nominatim(user_agent="to_explorer")

location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

print('The geograpical coordinates of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinates of Toronto are 43.653963, -79.387207.


In [122]:
# Creating a map of Toronto
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=9)

# Adding markers to the map
for lat, lng, borough, neighborhood in zip(toronto_dataframe['Latitude'], toronto_dataframe['Longitude'], toronto_dataframe['Borough'], toronto_dataframe['Neighbourhood']):
    label = '{}, {}'.format(toronto_dataframe, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

In [91]:
downtown_data = toronto_dataframe[toronto_dataframe['Borough'] == 'Downtown Toronto'].reset_index(drop=True)
downtown_data.head()

PostalCode           Borough    Neighbourhood   Latitude  Longitude
0        M5A  Downtown Toronto     Harbourfront  43.654260 -79.360636
1        M5B  Downtown Toronto          Ryerson  43.657162 -79.378937
2        M5B  Downtown Toronto  Garden District  43.657162 -79.378937
3        M5C  Downtown Toronto   St. James Town  43.651494 -79.375418
4        M5E  Downtown Toronto      Berczy Park  43.644771 -79.373306

In [92]:
address = 'Downtown Toronto'

geolocator = Nominatim(user_agent="to_explorer")

location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

print('The geograpical coordinates of Downtown Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinates of Downtown Toronto are 43.6563221, -79.3809161.


In [96]:
# Creating a map of Downtown Toronto using latitude and longitude values
map_downtown = folium.Map(location=[latitude, longitude], zoom_start=13)

# add markers to map
for lat, lng, label in zip(downtown_data['Latitude'], downtown_data['Longitude'], downtown_data['Neighbourhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_downtown)  
    
map_downtown

In [98]:
CLIENT_ID = 'JPQAWDB1LMR3OIPZLJF4MMCMFQQDHECU2ER3EH2V1NLNWJEV' # your Foursquare ID
CLIENT_SECRET = 'VGLOUHJ0TINOBNOMMBVAVJLN1055Y4QL0YVBQC44Y235XX2S' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: JPQAWDB1LMR3OIPZLJF4MMCMFQQDHECU2ER3EH2V1NLNWJEV
CLIENT_SECRET:VGLOUHJ0TINOBNOMMBVAVJLN1055Y4QL0YVBQC44Y235XX2S


In [100]:
LIMIT = 100
radius = 500

downtown_url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    latitude, 
    longitude, 
    radius, 
    LIMIT)

In [101]:
results = requests.get(downtown_url).json()
results

{'meta': {'code': 200, 'requestId': '5ddac77e7828ae001b95e19a'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Bay Street Corridor',
  'headerFullLocation': 'Bay Street Corridor, Toronto',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 129,
  'suggestedBounds': {'ne': {'lat': 43.6608221045, 'lng': -79.37470788695488},
   'sw': {'lat': 43.651822095499995, 'lng': -79.3871243130451}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '57eda381498ebe0e6ef40972',
       'name': 'UNIQLO ユニクロ',
       'location': {'address': '220 Yonge St',
        'crossStreet': 'at Dundas St W',
        'lat': 43.65591027779457,
        'lng': -79.38064099181345,
        'labeledLatLngs

In [102]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [103]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues)

filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name      categories        lat        lng
0          UNIQLO ユニクロ  Clothing Store  43.655910 -79.380641
1  Silver Snail Comics      Comic Shop  43.657031 -79.381403
2          Blaze Pizza     Pizza Place  43.656518 -79.380015
3   Ed Mirvish Theatre         Theater  43.655102 -79.379768
4  Yonge-Dundas Square           Plaza  43.656054 -79.380495

In [104]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            

        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            

        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [106]:
downtown_venues = getNearbyVenues(names=downtown_data['Neighbourhood'],
                                   latitudes=downtown_data['Latitude'],
                                   longitudes=downtown_data['Longitude']
                                  )

Harbourfront
Ryerson
Garden District
St. James Town
Berczy Park
Central Bay Street
Christie
Adelaide
King
Richmond
Harbourfront East
Toronto Islands
Union Station
Design Exchange
Toronto Dominion Centre
Commerce Court
Victoria Hotel
Harbord
University of Toronto
Chinatown
Grange Park
Kensington Market
CN Tower
Bathurst Quay
Island airport
Harbourfront West
King and Spadina
Railway Lands
South Niagara
Rosedale
Stn A PO Boxes 25 The Esplanade
Cabbagetown
St. James Town
First Canadian Place
Underground city
Church and Wellesley


In [107]:
print(downtown_venues.shape)
downtown_venues.head()

(2448, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Harbourfront               43.65426              -79.360636   
1  Harbourfront               43.65426              -79.360636   
2  Harbourfront               43.65426              -79.360636   
3  Harbourfront               43.65426              -79.360636   
4  Harbourfront               43.65426              -79.360636   

                    Venue  Venue Latitude  Venue Longitude  \
0        Roselle Desserts       43.653447       -79.362017   
1           Tandem Coffee       43.653559       -79.361809   
2  Cooper Koo Family YMCA       43.653191       -79.357947   
3     Body Blitz Spa East       43.654735       -79.359874   
4      Morning Glory Cafe       43.653947       -79.361149   

         Venue Category  
0                Bakery  
1           Coffee Shop  
2  Gym / Fitness Center  
3                   Spa  
4        Breakfast Spot

In [109]:
downtown_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                             
Adelaide                                           100   
Bathurst Quay                                       16   
Berczy Park                                         58   
CN Tower                                            16   
Cabbagetown                                         44   
Central Bay Street                                  83   
Chinatown                                           95   
Christie                                            17   
Church and Wellesley                                85   
Commerce Court                                     100   
Design Exchange                                    100   
First Canadian Place                               100   
Garden District                                    100   
Grange Park                                         95   
Harbord                                             35   
Harbourfront                                        48   
Harbourfront East                                  100   
Harbourfront West                                   16   
Island airport                                      16   
Kensington Market                                   95   
King                                               100   
King and Spadina                                    16   
Railway Lands                                       16   
Richmond                                           100   
Rosedale                                             4   
Ryerson                                            100   
South Niagara                                       16   
St. James Town                                     144   
Stn A PO Boxes 25 The Esplanade                     98   
Toronto Dominion Centre                            100   
Toronto Islands                                    100   
Underground city                                   100   
Union Station                                      100   
University of Toronto                               35   
Victoria Hotel                                     100   

                                 Neighborhood Longitude  Venue  \
Neighborhood                                                     
Adelaide                                            100    100   
Bathurst Quay                                        16     16   
Berczy Park                                          58     58   
CN Tower                                             16     16   
Cabbagetown                                          44     44   
Central Bay Street                                   83     83   
Chinatown                                            95     95   
Christie                                             17     17   
Church and Wellesley                                 85     85   
Commerce Court                                      100    100   
Design Exchange                                     100    100   
First Canadian Place                                100    100   
Garden District                                     100    100   
Grange Park                                          95     95   
Harbord                                              35     35   
Harbourfront                                         48     48   
Harbourfront East                                   100    100   
Harbourfront West                                    16     16   
Island airport                                       16     16   
Kensington Market                                    95     95   
King                                                100    100   
King and Spadina                                     16     16   
Railway Lands                                        16     16   
Richmond                                            100    100   
Rosedale                                              4      4   
Ryerson                                             100    100   
South Niagara                         

In [110]:
# one hot encoding
downtown_onehot = pd.get_dummies(downtown_venues[['Venue Category']], prefix="", prefix_sep="")

# adding neighborhood column back to dataframe
downtown_onehot['Neighborhood'] = downtown_venues['Neighborhood'] 

# moving neighborhood column to the first column
fixed_columns = [downtown_onehot.columns[-1]] + list(downtown_onehot.columns[:-1])
downtown_onehot = downtown_onehot[fixed_columns]

downtown_onehot.head()

Yoga Studio  Afghan Restaurant  Airport  Airport Food Court  Airport Gate  \
0            0                  0        0                   0             0   
1            0                  0        0                   0             0   
2            0                  0        0                   0             0   
3            0                  0        0                   0             0   
4            0                  0        0                   0             0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Art Gallery  Arts & Crafts Store  Asian Restaurant  \
0             0         0            0                    0                 0   
1             0         0            0                    0                 0   
2             0         0            0                    0                 0   
3             0         0            0                    0                 0   
4             0         0            0                    0                 0   

   Athletics & Sports  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0                   0          0           0           0       1     0    0   
1                   0          0           0           0       0     0    0   
2                   0          0           0           0       0     0    0   
3                   0          0           0           0       0     0    0   
4                   0          0           0           0       0     0    0   

   Baseball Stadium  Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  \
0                 0                   0      0                0         0   
1                 0                   0      0                0         0   
2                 0                   0      0                0         0   
3                 0                   0      0                0         0   
4                 0                   0      0                0         0   

   Beer Store  Belgian Restaurant  Bistro  Boat or Ferry  Bookstore  \
0           0                   0       0              0          0   
1           0                   0       0              0          0   
2           0                   0       0              0          0   
3           0                   0       0              0          0   
4           0                   0       0              0          0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bubble Tea Shop  Building  \
0                     0               0        0                0         0   
1                     0               0        0                0         0   
2                     0               0        0                0         0   
3                     0               0        0                0         0   
4                     0               1        0                0         0   

   Burger Joint  Burrito Place  Butcher  Café  Candy Store  \
0             0              0        0     0            0   
1             0              0        0     0            0   
2             0              0        0     0            0   
3             0              0        0     0            0   
4             0              0        0     0            0   

   Caribbean Restaurant  Cheese Shop  Chinese Restaurant  Chocolate Shop  \
0                     0            0                   0               0   
1                     0            0                   0               0   
2                     0            0                   0               0   
3                     0            0                   

In [111]:
downtown_onehot.shape

(2448, 203)

In [120]:
downtown_grouped = downtown_onehot.groupby('Neighborhood').mean().reset_index()
downtown_grouped.head()

Neighborhood  Yoga Studio  Afghan Restaurant  Airport  Airport Food Court  \
0       Adelaide          0.0                0.0   0.0000              0.0000   
1  Bathurst Quay          0.0                0.0   0.0625              0.0625   
2    Berczy Park          0.0                0.0   0.0000              0.0000   
3       CN Tower          0.0                0.0   0.0625              0.0625   
4    Cabbagetown          0.0                0.0   0.0000              0.0000   

   Airport Gate  Airport Lounge  Airport Service  Airport Terminal  \
0        0.0000           0.000           0.0000             0.000   
1        0.0625           0.125           0.1875             0.125   
2        0.0000           0.000           0.0000             0.000   
3        0.0625           0.125           0.1875             0.125   
4        0.0000           0.000           0.0000             0.000   

   American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0             0.030000           0.0       0.0     0.000000   
1             0.000000           0.0       0.0     0.000000   
2             0.000000           0.0       0.0     0.017241   
3             0.000000           0.0       0.0     0.000000   
4             0.022727           0.0       0.0     0.000000   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  BBQ Joint  \
0                  0.0              0.03                 0.0   0.000000   
1                  0.0              0.00                 0.0   0.000000   
2                  0.0              0.00                 0.0   0.017241   
3                  0.0              0.00                 0.0   0.000000   
4                  0.0              0.00                 0.0   0.000000   

   Baby Store  Bagel Shop    Bakery      Bank     Bar  Baseball Stadium  \
0         0.0    0.000000  0.030000  0.000000  0.0400               0.0   
1         0.0    0.000000  0.000000  0.000000  0.0625               0.0   
2         0.0    0.017241  0.051724  0.000000  0.0000               0.0   
3         0.0    0.000000  0.000000  0.000000  0.0625               0.0   
4         0.0    0.000000  0.045455  0.022727  0.0000               0.0   

   Basketball Stadium     Beach  Bed & Breakfast  Beer Bar  Beer Store  \
0            0.000000  0.000000              0.0  0.000000    0.000000   
1            0.000000  0.000000              0.0  0.000000    0.000000   
2            0.017241  0.017241              0.0  0.034483    0.000000   
3            0.000000  0.000000              0.0  0.000000    0.000000   
4            0.000000  0.000000              0.0  0.000000    0.022727   

   Belgian Restaurant    Bistro  Boat or Ferry  Bookstore  \
0                 0.0  0.000000         0.0000       0.02   
1                 0.0  0.000000         0.0625       0.00   
2                 0.0  0.017241         0.0000       0.00   
3                 0.0  0.000000         0.0625       0.00   
4                 0.0  0.000000         0.0000       0.00   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bubble Tea Shop  Building  \
0                  0.01        0.030000      0.0              0.0       0.0   
1                  0.00        0.000000      0.0              0.0       0.0   
2                  0.00        0.017241      0.0              0.0       0.0   
3                  0.00        0.000000      0.0              0.0       0.0   
4                  0.00        0.022727      0.0              0.0       0.0   

   Burger Joint  Burrito Place   Butcher      Café  Candy Store  \
0          0.03           0.01  0.000000  0.050000          0.0   
1          0.00           0.00  0.000000  0.000000          0.0   
2          0.00           0.00  0.017241  0.034483          0.0   
3          0.00           0.00  0.000000  0.000000          0.0   
4          0.00           0.00  0.022727  0.045455          0.0   

   Caribbean Restaurant  Cheese Shop  Chinese Restaurant  Chocolate Shop  \
0              0.000000     0.000000            0

In [115]:
num_top_venues = 10

for hood in downtown_grouped['Neighborhood']:
    print("----------"+hood+"----------")
    temp = downtown_grouped[downtown_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----------Adelaide----------
              venue  freq
0       Coffee Shop  0.07
1              Café  0.05
2        Steakhouse  0.04
3               Bar  0.04
4   Thai Restaurant  0.04
5  Sushi Restaurant  0.03
6      Burger Joint  0.03
7    Breakfast Spot  0.03
8        Restaurant  0.03
9    Cosmetics Shop  0.03


----------Bathurst Quay----------
              venue  freq
0   Airport Service  0.19
1    Airport Lounge  0.12
2  Airport Terminal  0.12
3     Boat or Ferry  0.06
4             Plane  0.06
5  Sculpture Garden  0.06
6       Coffee Shop  0.06
7   Harbor / Marina  0.06
8               Bar  0.06
9      Airport Gate  0.06


----------Berczy Park----------
                venue  freq
0         Coffee Shop  0.09
1              Bakery  0.05
2        Cocktail Bar  0.03
3  Seafood Restaurant  0.03
4            Beer Bar  0.03
5                Café  0.03
6         Cheese Shop  0.03
7          Steakhouse  0.03
8      Farmers Market  0.03
9          Restaurant  0.02


----------CN Tower-

In [118]:
# Creating a function to define the top venues in the area being explored

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [119]:
num_top_venues = 3

indicators = ['st', 'nd', 'rd']

# creating columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# creating a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = downtown_grouped['Neighborhood']

for ind in np.arange(downtown_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(downtown_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Adelaide           Coffee Shop                  Café   
1  Bathurst Quay       Airport Service      Airport Terminal   
2    Berczy Park           Coffee Shop                Bakery   
3       CN Tower       Airport Service      Airport Terminal   
4    Cabbagetown           Coffee Shop            Restaurant   

  3rd Most Common Venue  
0            Steakhouse  
1        Airport Lounge  
2            Steakhouse  
3        Airport Lounge  
4    Italian Restaurant

## 3.2) Clustering Neighborhoods in Downtown Toronto

In [140]:
# Setting number of clusters
kclusters = 5

downtown_grouped_clustering = downtown_grouped.drop('Neighborhood', 1)

# Running k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(downtown_grouped_clustering)

# Checking cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 2, 0, 2, 0, 0, 3, 4, 0, 0], dtype=int32)

In [141]:
downtown_merged = downtown_data

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
downtown_merged = downtown_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

downtown_merged.head()

PostalCode           Borough     Neighborhood   Latitude  Longitude  \
0        M5A  Downtown Toronto     Harbourfront  43.654260 -79.360636   
1        M5B  Downtown Toronto          Ryerson  43.657162 -79.378937   
2        M5B  Downtown Toronto  Garden District  43.657162 -79.378937   
3        M5C  Downtown Toronto   St. James Town  43.651494 -79.375418   
4        M5E  Downtown Toronto      Berczy Park  43.644771 -79.373306   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0               0           Coffee Shop                Bakery   
1               0           Coffee Shop        Clothing Store   
2               0           Coffee Shop        Clothing Store   
3               0           Coffee Shop            Restaurant   
4               0           Coffee Shop                Bakery   

  3rd Most Common Venue  
0                  Park  
1                Bakery  
2                Bakery  
3                  Café  
4            Steakhouse

In [142]:
# Creating map of clustered Neighborhoods
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=13)

# Color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# Adding markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(downtown_merged['Latitude'], downtown_merged['Longitude'], downtown_merged['Neighborhood'], downtown_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters